In [1]:
# Description: In this version of the algorithm, the voxels are checked for both background and color consistency using the provided 
# datasets (i.e. after projecting a voxel to the RGB images and silhouettes, it is carved out if it turned out to be at least 
# non-background consistent or non-color consistent) 

import os
import cv2
import math
import numpy as np 
from numpy import savetxt, genfromtxt

import silhouette_extract
import projection
import radiance_max_dist
import radiance_std


#Setting the path
data_dir = os.path.expanduser('~')
data_dir = data_dir + "/Downloads/DataSets/bird_data/images/"

#Dimensions of the initial canvas of voxels 

# Dimensions for Beethoven's head           
step_size = 0.25
xmin = -8
xmax = 5
ymin = -8
ymax = 8
zmin = -5
zmax = 16 #17.5

#Dimensions for Bunny

#Dimensions for Bird

#Dimensions for Pig



total_voxels=int((xmax-xmin)/step_size)*int((ymax-ymin)/step_size)*int((zmax-zmin)/step_size)

#Image dimensions
height = 768
width = 1024

#Initial canvas of voxels defined as a three dimentional array of true booleans
obj = np.ones((int((xmax-xmin)/step_size), int((ymax-ymin)/step_size), int((zmax-zmin)/step_size)), dtype = bool)


out_cnt = 0
carve_cnt = 0
bkgrnd_image_pixel_mark_situ = {}
color_image_pixel_mark_situ = {}
silhouettes = {}
camera_projections = {}
images = {}
for file in os.listdir(data_dir):
    #Initializing the pixel marking matrix to account for voxels occlusion from some camera views
    bkgrnd_pixel_map = np.zeros((height, width), dtype = np.int8)
    color_pixel_map = np.zeros((height, width), dtype = np.int8)
    bkgrnd_image_pixel_mark_situ[file] = bkgrnd_pixel_map
    color_image_pixel_mark_situ[file] = color_pixel_map
    silhouettes[file] = silhouette_extract.get_mask(file)
    camera_projections[file] = projection.projectionMatrix(file)
    images[file] = cv2.imread(data_dir + file)
#Method to check the voxel consistency using only the background constraint
def background_consistency_check(i, j, k):
    global out_cnt, bkgrnd_image_pixel_mark_situ
    bkgrd_consist = True
    voxel_cord = np.array([[xmin + i*step_size], [ymin + j*step_size],[zmin + k*step_size], [1]])

    for file in os.listdir(data_dir):
        #Reading each image's segmentation and projection matrix    
        img_mask = silhouettes[file]
        P = camera_projections[file]
        #Projecting the voxel on the 2D image
        pix_cord = P.dot(voxel_cord)
        pix_cord = pix_cord / pix_cord[2,0] # division by the last vector's element of the
                                                        # homogeneous representation to get the pixel's coordinates in the
                                                        #extracted image

        #if the voxel is projected outside the 2D image boundaries, this means that the voxel is not in the camera's visual field
        #and the info provided by the correspondent 2D image cannot be used
        if pix_cord[1,0] >= height or pix_cord[0,0] < 0 or pix_cord[0,0] >= width or pix_cord[1,0] < 0:
            out_cnt = out_cnt+1
            continue    
        
        if bkgrnd_image_pixel_mark_situ[file][int(pix_cord[1,0]), int(pix_cord[0,0])] == 0:
            # Pixels with intensity values 0 (black) denote object occupancy
            if img_mask[int(pix_cord[1,0]), int(pix_cord[0,0]), 0] > 0 or img_mask[int(pix_cord[1,0]), int(pix_cord[0,0]), 1] > 0 or img_mask[int(pix_cord[1,0]), int(pix_cord[0,0]), 2] > 0:
                #If the pixel is part of the background (i.e. not black or white in this case), it will be carved out
                bkgrd_consist = False
                break
        
    if not bkgrd_consist:
        return False
    else:
        
        # area block. This idea is implemented to avoid the extraction and the inclusion in the 
        # calculation of the projected pixel's color from an image where the correspondent voxel cannot be seen
        # in the first place (i.e. the correspondent voxel is hidden by another voxel that was previously proven
        # to be consistent)
        voxel_cord1 = np.array([[xmin + i*step_size+step_size], [ymin + j*step_size+step_size],[zmin + k*step_size+step_size], [1]])
        for file in os.listdir(data_dir):
            P = camera_projections[file]
            pix_cord = P.dot(voxel_cord)
            pix_cord = pix_cord / pix_cord[2,0]
            if pix_cord[1,0] >= height or pix_cord[0,0] < 0 or pix_cord[0,0] >= width or pix_cord[1,0] < 0:
                continue 
            if bkgrnd_image_pixel_mark_situ[file][int(pix_cord[1,0]), int(pix_cord[0,0])] == 0:
               pix_cord1 = P.dot(voxel_cord1)
               pix_cord1 = pix_cord1 / pix_cord1[2,0]
               pix_length = int(np.linalg.norm(pix_cord-pix_cord1))
        
               for m in range(int(pix_cord[1,0]-pix_length/2),int(pix_cord[1,0] + pix_length/2)):
                    for n in range(int(pix_cord[0,0]-pix_length/2),int(pix_cord[0,0] + pix_length/2)):
                        if ((m>=height or m<0) or (n>=width or n<0)):
                            continue
                        else:
                            bkgrnd_image_pixel_mark_situ[file][m,n] = 100 #any other non-zero number can be placed here
        return True 

#Method to check the voxel consistency using only the Lambertian color constraint
def color_consistency_check(i, j, k):
    global color_image_pixel_mark_situ
    color_consist = True

    color_set = np.empty([len(images), 3])
    c = 0
    voxel_cord = np.array([[xmin + i*step_size], [ymin + j*step_size],[zmin + k*step_size], [1]])

    for file in os.listdir(data_dir):
        img = images[file]
        pix_cord = camera_projections[file].dot(voxel_cord)
        pix_cord = pix_cord / pix_cord[2,0]

        if pix_cord[1,0] >= height or pix_cord[0,0] < 0 or pix_cord[0,0] >= width or pix_cord[1,0] < 0:
            continue    
        
        if color_image_pixel_mark_situ[file][int(pix_cord[1,0]), int(pix_cord[0,0])] == 0:
            color_set[c] = img[int(pix_cord[1,0]), int(pix_cord[0,0])]
            c = c+1
    if c == 0:
        return True
    if c != len(images):
        #print("Color set before splitting: ", color_set)
        color_set = np.split(color_set, [c, len(images)], axis = 0)[0]
        #print("Color Set: ", color_set)
    color_consist, color = radiance_max_dist.consistency(color_set)
    #color_consist, color = radiance_std.consistency(color_set)
    
    if not color_consist:
        return False
    else:
        
        # area block. This idea is implemented to avoid the extraction and the inclusion in the 
        # calculation of the projected pixel's color from an image where the correspondent voxel cannot be seen
        # in the first place (i.e. the correspondent voxel is hidden by another voxel that was previously proven
        # to be consistent)
        voxel_cord1 = np.array([[xmin + i*step_size+step_size], [ymin + j*step_size+step_size],[zmin + k*step_size+step_size], [1]])
        for file in os.listdir(data_dir):
            pix_cord = camera_projections[file].dot(voxel_cord)
            pix_cord = pix_cord / pix_cord[2,0]
            if pix_cord[1,0] >= height or pix_cord[0,0] < 0 or pix_cord[0,0] >= width or pix_cord[1,0] < 0:
                continue 
            if color_image_pixel_mark_situ[file][int(pix_cord[1,0]), int(pix_cord[0,0])] == 0:
                pix_cord1 = camera_projections[file].dot(voxel_cord1)
                pix_cord1 = pix_cord1 / pix_cord1[2,0]
                pix_length = int(np.linalg.norm(pix_cord-pix_cord1))
        
                for m in range(int(pix_cord[1,0]-pix_length/2),int(pix_cord[1,0] + pix_length/2)):
                    for n in range(int(pix_cord[0,0]-pix_length/2),int(pix_cord[0,0] + pix_length/2)):
                        if ((m>=height or m<0) or (n>=width or n<0)):
                            continue
                        else:
                            color_image_pixel_mark_situ[file][m,n] = 100 #any other non-zero number can be placed here
        return True       

if __name__ == "__main__":
    voxel_count = 0
    eval_list = []
    # carving out the visual hull
    for i in range(obj.shape[0]):
        for j in range(obj.shape[1]):
            for k in range(obj.shape[2]):
                voxel_count +=1
                print("processed "+ str(voxel_count/total_voxels*100) + "% of voxels")

                
                background_consistency = background_consistency_check(i, j, k)
                color_consistency = color_consistency_check(i,j,k)

                if (not background_consistency or not color_consistency):
                    obj[i,j,k] = 0
                    carve_cnt = carve_cnt+1  
    #Saving the output 3D shape that was carved from the initial canvas of voxels as a .txt file
    print("Object size before carving: ",obj.size,"Object size after carving: ", obj.size-carve_cnt,"Out count: ", out_cnt)
    final_file = open("./bkgrnd_and_color_visual_hull_result.txt", "w")
    head_line = "{} {} {} {} {} {} {} {}\n" # step_size, xmin, xmax, ymin, ymax, zmin, zmax, is_colored version
    voxel_elem = "{} "
    final_file.write(head_line.format(step_size, xmin, xmax, ymin, ymax, zmin, zmax, 0))
            
    for i in range(obj.shape[0]):
        for j in range(obj.shape[1]):
            for k in range(obj.shape[2]):
                final_file.write(voxel_elem.format(int(obj[i,j,k])))
                eval_list.append(int(obj[i,j,k]))  

    final_file.close()
    eval_array = np.array(eval_list)
    savetxt('bkgrd_and_color.csv',eval_array,delimiter=',')                                   
# end of the visual hull build


processed 0.00035771520146520144% of voxels
processed 0.0007154304029304029% of voxels
processed 0.0010731456043956045% of voxels
processed 0.0014308608058608058% of voxels
processed 0.0017885760073260075% of voxels
processed 0.002146291208791209% of voxels
processed 0.00250400641025641% of voxels
processed 0.0028617216117216115% of voxels
processed 0.0032194368131868135% of voxels
processed 0.003577152014652015% of voxels
processed 0.003934867216117216% of voxels
processed 0.004292582417582418% of voxels
processed 0.004650297619047619% of voxels
processed 0.00500801282051282% of voxels
processed 0.005365728021978022% of voxels
processed 0.005723443223443223% of voxels
processed 0.006081158424908425% of voxels
processed 0.006438873626373627% of voxels
processed 0.006796588827838828% of voxels
processed 0.00715430402930403% of voxels
processed 0.007512019230769231% of voxels
processed 0.007869734432234432% of voxels
processed 0.008227449633699634% of voxels
processed 0.00858516483516483

KeyboardInterrupt: 

Background constraint only ==> Object size before carving:  279552 Object size after carving:  81428 Out count:  39162

Background and color (distance threshold = 0) ==> Object size before carving:  279552 Object size after carving:  81416 Out count:  39162

Background and color (distance threshold = 10) ==> Object size before carving:  279552 Object size after carving:  81479 Out count:  39171

Background and color (distance threshold = 0) ==> Object size before carving:  279552 Object size after carving:  81416 Out count:  39162

background_consistency, color_consistency, check background_constraint only ==> Object size before carving:  279552 Object size after carving:  81387 Out count:  39156

background_consistency, check background_constraint only ==> Object size before carving:  279552 Object size after carving:  81387 Out count:  39156

 color_consistency, background_consistency, check background_constraint only ==> Object size before carving:  279552 Object size after carving:  81387 Out count:  39156

 color_consistency, background_consistency, check background_constraint and color_constraint (distance_threshold = 10) ==> Object size before carving:  279552 Object size after carving:  0 Out count:  39156